In [7]:
# Install Yahoo Finance for get data
!pip install yfinance
!pip install mpl_finance
!pip install pandas
!pip install jupyter-dash
!pip install plotly

In [10]:
#Let’s import some useful libraries and initialize the plotting environment.
import pandas as pd
import numpy as np
import yfinance
import plotly.graph_objects as go
import pandas as pd


In [29]:
#Now we can plot every coin
# name = 'BNB-USD'
def display_candlestick(df,name, interval, start, end):
  """
  args: name can be every cryptocurrnecy on Yahoo finance
  """
  fig = go.Figure(go.Candlestick(
      x=df.index,
      open=df['Open'],
      high=df['High'],
      low=df['Low'],
      close=df['Close']))

  fig.update_layout(xaxis_rangeslider_visible=False)

  fig.show()
name = 'ETH-USD'
interval = "1d"
start="2021-06-15"
end="2022-3-07"
ticker = yfinance.Ticker(name)
df = ticker.history(name,interval,start, end).drop(['Dividends','Stock Splits'],axis=1)
display_candlestick(df,name, interval, start, end)
df

Open         High          Low        Close       Volume
Date                                                                       
2021-06-14  2508.770508  2606.432861  2469.388184  2537.891113  26964576331
2021-06-15  2587.762695  2639.229248  2515.153076  2610.936768  29005279219
2021-06-16  2544.864746  2554.628906  2354.350586  2367.663574  24101926180
2021-06-17  2367.306396  2457.175537  2312.301514  2372.001953  21871633186
2021-06-18  2374.586914  2377.195068  2147.308350  2231.733154  22752818388
...                 ...          ...          ...          ...          ...
2022-03-02  2972.471924  3026.868164  2919.943115  2950.118408  16636517503
2022-03-03  2950.156738  2964.673340  2797.319336  2834.468994  13091199728
2022-03-04  2834.987305  2835.176270  2587.748291  2617.156006  14496939024
2022-03-05  2618.473633  2679.102539  2596.989990  2664.831055   8072368396
2022-03-06  2664.943604  2673.637207  2555.037354  2555.037354   8872976607

[266 rows x 5 columns]

In [30]:
#Let’s not create two functions that identify the 4-candles fractals.
def isSupport(df,i):
  support = df['Low'][i] < df['Low'][i-1]  and df['Low'][i] < df['Low'][i+1] and df['Low'][i+1] < df['Low'][i+2] and df['Low'][i-1] < df['Low'][i-2]
  return support
def isResistance(df,i):
  resistance = df['High'][i] > df['High'][i-1]  and df['High'][i] > df['High'][i+1] and df['High'][i+1] > df['High'][i+2] and df['High'][i-1] > df['High'][i-2]
  return resistance

In [31]:
"""
Finally, let’s create a list that will contain the levels we find.
Each level is a tuple whose first element is the index of the signal candle and the second element is the price value.
"""
df
levels = []
for i in range(2,df.shape[0]-2):
  if isSupport(df,i):
    levels.append((i,df['Low'][i]))
  elif isResistance(df,i):
    levels.append((i,df['High'][i]))
levels

[(8, 1707.6005859375),
 (12, 1719.5594482421875),
 (16, 2282.989013671875),
 (18, 2021.8248291015625),
 (23, 2403.7734375),
 (25, 2051.066650390625),
 (36, 1722.05078125),
 (48, 2695.429443359375),
 (50, 2449.353515625),
 (65, 2959.0283203125),
 (73, 3060.228759765625),
 (77, 3151.444580078125),
 (94, 3673.310791015625),
 (99, 2676.407470703125),
 (105, 3163.6650390625),
 (107, 2786.98828125),
 (116, 3667.95751953125),
 (119, 3385.76171875),
 (124, 3962.453125),
 (140, 4160.966796875),
 (142, 4664.91015625),
 (157, 3959.227783203125),
 (178, 4482.31396484375),
 (199, 3595.204833984375),
 (204, 3876.78515625),
 (212, 3401.219970703125),
 (216, 3376.401123046875),
 (232, 2802.3154296875),
 (234, 2587.783447265625),
 (241, 3271.316162109375),
 (245, 2840.257568359375),
 (246, 3185.520751953125),
 (260, 3029.651611328125)]

In [32]:
def detect_green_candle(df, i):
  if df['Open'][i]< df['Close'][i]:
    return True
  else:
    return False
#We can now define a function that plots price and key levels together.
def plot_all(levels):
    fig = go.Figure(go.Candlestick(
      x=df.index,
      open=df['Open'],
      high=df['High'],
      low=df['Low'],
      close=df['Close']))
    df2 = df.copy()
    df2 = df2.reset_index()
    for level in levels:
      # plt.hlines(level[1],xmin  =df['Date'][level[0]],\
      # xmax=max(df['Date']),colors='blue')
      if detect_green_candle(df, level[0]):
        shapes = [
                  dict(
                      x0=df2.iloc[level[0]]['Date'],
                      x1=df.index[-1],
                      y0=level[1],
                      y1=df2.iloc[level[0]]['Close'],
                      xref='x',
                      yref='y',
                      line_width=2,
                       )
                  ]
      else:
        shapes = [
                  dict(x0=df2.iloc[level[0]]['Date'],
                       x1=max(df.index),
                       y0=level[1],
                       y1=df2.iloc[level[0]]['Open'],
                       xref='x',
                       yref='y',
                       line_width=2
                       )
                  ]
      fig.update_layout(
      title='The Great Recession',
      yaxis_title='AAPL Stock',
      shapes = shapes)
      fig.show()
plot_all(levels)

In [33]:
df['Volume'].idxmax()

Timestamp('2021-09-07 00:00:00')

In [34]:
"""
As you can see, we have been able to detect the major rejection levels,
but there’s still some noise. Some levels are over others, but they are essentially the same level.
We can clean this noise modifying the function that detects key levels.
If a level is near another one, it will be discarded. We must decide what “near” means,
then. We can say that a level is near another one if their distance is less than the average candle size in
our chart (i.e. the average difference between high and low prices in a candle). This will give us a rough estimate of volatility.
"""
s =  np.mean(df['High'] - df['Low'])

In [35]:
#Let’s define a function that, given a price value, returns False if it is near some previously discovered key level.
def isFarFromLevel(l):
   return np.sum([abs(l-x) < s  for x in levels]) == 0

In [36]:
#Now we can scan the price history looking for key levels using this function as a filter.
# levels = []
# for i in range(2,df.shape[0]-2):
#   if isSupport(df,i):
#     # if detect_green_candle:
#     l = df['Close'][i]
#     # else:
#     #   l = df['Open'][i]
#     if isFarFromLevel(l):
#       levels.append((i,l))
#   elif isResistance(df,i):
#     # if detect_green_candle:
#       # l = df['Close'][i]
#     # else:
#     l = df['Open'][i]
#     if isFarFromLevel(l):
#       levels.append((i,l))

In [37]:
plot_all(levels)

In [23]:
levels2 = [levels[i][0] for i in range(len(levels))]
dfImportantZone = df.filter(items=levels2,axis=0)


In [24]:
levels2

[8, 12, 16, 18, 23, 25, 36, 48, 50, 65, 73, 77, 94, 99, 105, 107]

In [25]:
# last_day = df.iloc[-1]

# # df['Exist_in_levels'] = ""

In [38]:
df_temp = df.reset_index()
Filter_df = df_temp.filter(items=levels2, axis=0)

In [39]:
Filter_df


Date         Open         High          Low        Close  \
8   2021-06-22  1886.667603  1993.159790  1707.600586  1874.950073   
12  2021-06-26  1810.884277  1850.179810  1719.559448  1829.239258   
16  2021-06-30  2164.216309  2282.989014  2090.760742  2274.547607   
18  2021-07-02  2109.892578  2155.596436  2021.824829  2150.040283   
23  2021-07-07  2323.208496  2403.773438  2298.026855  2315.161865   
25  2021-07-09  2115.573975  2185.376221  2051.066650  2146.692383   
36  2021-07-20  1819.082031  1836.998047  1722.050781  1787.510742   
48  2021-08-01  2530.462891  2695.429443  2520.931885  2561.852051   
50  2021-08-03  2609.413086  2630.314209  2449.353516  2502.349609   
65  2021-08-18  3011.963623  3124.976074  2959.028320  3020.089844   
73  2021-08-26  3228.747314  3249.655273  3060.228760  3100.325439   
77  2021-08-30  3227.192627  3346.581055  3151.444580  3224.374268   
94  2021-09-16  3613.073730  3673.310791  3489.805664  3571.294922   
99  2021-09-21  2977.310547  3101.697510  2676.407471  2764.431152   
105 2021-09-27  3065.837891  3163.665039  2932.692871  2934.138916   
107 2021-09-29  2809.297607  2946.881348  2786.988281  2853.143311   

          Volume  
8    35547251725  
12   20637542361  
16   25828056268  
18   31796212554  
23   22398345285  
25   23029574602  
36   17368597636  
48   22697987055  
50   22696753413  
65   21539248425  
73   17405668117  
77   19306924485  
94   20093903064  
99   30405062665  
105  19164053681  
107  15763456158

In [40]:
# Filter df if last df exist in levels return that level
last_day_Open = df.iloc[-1]['Open']
last_day_High =  df.iloc[-1]['High']
last_day_Close =  df.iloc[-1]['Close']
last_day_Low =  df.iloc[-1]['Low']
Filter_df[(last_day_Open <= Filter_df['High']) & (last_day_Open >= Filter_df['Low'])|
          (last_day_Close <= Filter_df['High']) & (last_day_Close <= Filter_df['Low'])|
          (last_day_Low <= Filter_df['High']) & (last_day_Low <= Filter_df['Low'])|
          (last_day_High <= Filter_df['High']) & (last_day_High <= Filter_df['Low'])
          ]

Date         Open         High          Low        Close  \
48  2021-08-01  2530.462891  2695.429443  2520.931885  2561.852051   
65  2021-08-18  3011.963623  3124.976074  2959.028320  3020.089844   
73  2021-08-26  3228.747314  3249.655273  3060.228760  3100.325439   
77  2021-08-30  3227.192627  3346.581055  3151.444580  3224.374268   
94  2021-09-16  3613.073730  3673.310791  3489.805664  3571.294922   
99  2021-09-21  2977.310547  3101.697510  2676.407471  2764.431152   
105 2021-09-27  3065.837891  3163.665039  2932.692871  2934.138916   
107 2021-09-29  2809.297607  2946.881348  2786.988281  2853.143311   

          Volume  
48   22697987055  
65   21539248425  
73   17405668117  
77   19306924485  
94   20093903064  
99   30405062665  
105  19164053681  
107  15763456158

In [ ]:
print()
